<a href="https://colab.research.google.com/github/jopelle/Practica3_Ingenieria_Software/blob/master/Probando.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Preparación del dataset**

Importamos las librerias que van a ser necesarias para realizar esta práctica

In [0]:
import sys
from fastai.text import *
import html
import json
import numpy as np
from pathlib import Path

Descomprimimos la libreria noticias 

In [5]:
!unzip noticias.zip -d noticias

Archive:  noticias.zip
  inflating: noticias/noticias2016_0.json  
  inflating: noticias/noticias2016_1.json  
  inflating: noticias/noticias2016_2.json  
  inflating: noticias/noticias2016_3.json  
  inflating: noticias/noticias2016_4.json  
  inflating: noticias/noticias2016_5.json  
  inflating: noticias/noticias2016_6.json  
  inflating: noticias/noticias2016_7.json  
  inflating: noticias/noticias2016_8.json  
  inflating: noticias/noticias2016_9.json  


Mostramos todos los nombres de los ficheros que se encuentran en nuestra carpeta noticias.

Guardamos el contenido de los ficheros en la variable jsons.

In [6]:
path=Path('./noticias')
jsons=[]
for file in path.iterdir():
    print(file)
    for line in open(file, 'r', encoding="utf-8"):
        jsons.append(json.loads(line))

noticias/noticias2016_6.json
noticias/noticias2016_2.json
noticias/noticias2016_3.json
noticias/noticias2016_9.json
noticias/noticias2016_1.json
noticias/noticias2016_8.json
noticias/noticias2016_4.json
noticias/noticias2016_0.json
noticias/noticias2016_5.json
noticias/noticias2016_7.json


Ahora tenemos el contenido de cada fichero json en una componente de la varialbe jsons.

Mostramos los keys de los json

In [7]:
jsons[0].keys()

dict_keys(['help', 'success', 'result'])

Nos interesa el contenido de 'result', ya que los otros no aportan mucho.


In [8]:
jsons[0]['result'].keys()

dict_keys(['count', 'sort', 'facets', 'results', 'search_facets'])

In [9]:
for k in jsons[0]['result'].keys():
    print(k, type(jsons[0]['result'][k]))

count <class 'int'>
sort <class 'str'>
facets <class 'dict'>
results <class 'list'>
search_facets <class 'dict'>


In [10]:
jsons[0]['result']['facets']

{}

In [11]:
jsons[0]['result']['results']

[{'author': None,
  'author_email': None,
  'colabora': [],
  'creator_user_id': 'c1125728-f49f-47ff-bef4-06400ac320be',
  'creator_username': 'actualidad',
  'dato_abierto': '{}',
  'descripcion': '',
  'destacado': '',
  'destacados_secciones': [],
  'destinatarios': ['Ciudadanos'],
  'editor': ['Unidad de imagen institucional'],
  'editor_post': [],
  'ejes_de_gobierno': [],
  'eliminado': '',
  'eliminados_secciones': [],
  'enlaces_relacionados': [],
  'fecha_creacion': '2018-07-27T11:53:19Z',
  'formato': 'html',
  'groups': [],
  'id': '08c717ff-5b17-463f-8b4e-a98e02d30d0c',
  'idioma': 'spa',
  'isopen': False,
  'licencia': 'cc-by',
  'license_id': None,
  'license_title': None,
  'localizacion': ['La Rioja'],
  'localizacion_hidden': ['La Rioja'],
  'maintainer': None,
  'maintainer_email': None,
  'metadata_created': '2018-07-27T11:52:49.258940',
  'metadata_modified': '2018-10-25T18:24:43.522509',
  'multimedia': '',
  'name': 'not-el-gobierno-riojano-invertira-mas-de-450-0

Como podemos ver, en 'results' tenemos una lista con la información de cada noticia.

In [12]:
type(jsons[0]['result']['results'][0])

dict

La descripción de las noticias es la información que nos interesa y las descripciones serán nuestras clases

In [0]:
etiquetas = []
descripciones = []
organizaciones = []

for ficheroJson in jsons:
    for noticia in ficheroJson['result']['results']:
        if 'organizacion' in noticia and len(noticia[org])==1 and len(noticia[desc])>0:
            etiquetas.append(noticia[org][0])
            descripciones.append(noticia[desc])
            organizaciones.append(noticia[org][0])

Transformamos las organizaciones en números enteros

In [0]:
def labels_to_num(tags, labels_dict):
    labels = [labels_dict[i] for i in tags]
    labels = np.array(labels)
    return labels

str_labels = set(etiquetas)
labels_dict = {tag: i for i, tag in enumerate(str_labels)}

etiquetas = labels_to_num(etiquetas, labels_dict)

Con el siguiente código "limpiamos" las descripciones de elementos html

In [0]:
def cleanhtml(raw_html):
  cleanr = re.compile('<.*?>')
  cleantext = re.sub(cleanr, '', raw_html)
  return cleantext

In [0]:
def limpiarDescripcion(descs):
  descsBien = []
  for i in range(len(descs)):
      a = cleanhtml(descs[i])
      a = a.replace("\r\n"," ")
      a = html.unescape(a)
      a = a.strip()
      descsBien.append(a)
  return descsBien

In [0]:
descBien = limpiarDescripcion(descripciones)

In [0]:
np.random.seed(42)

trn_idx = np.random.permutation(len(descripciones))

descripciones = np.array(descBien)[trn_idx]
organizaciones = np.array(organizaciones)[trn_idx]
etiquetas = np.array(etiquetas)[trn_idx]

In [0]:
col_names = ['organizacion','descripcion']

In [29]:
print(descripciones[:5])

['El director general de Cultura y Turismo, Eduardo Rodríguez Osés, ha presidido esta mañana en Riojaforum un encuentro con los principales agentes culturales del de La Rioja, con el objetivo de crear una red de trabajo y colaboración conjunta entre las diversas instituciones riojanas y las empresas profesionales de las artes escénicas en La Rioja. Con ello se busca promocionar la "marca teatro riojano" y facilitar el acceso de este sector a los circuitos de teatro de todo el ámbito nacional.Asimismo, en esta reunión, organizada por la Consejería de Desarrollo Económico e Innovación y la Asociación de compañías profesionales de las Artes Escénicas en La Rioja \'Aescena\', se ha resaltado la profesionalidad de las compañías de las Artes Escénicas como motor de desarrollo económico, así como su condición de empresas, con sus derechos y obligaciones, que hacen de las Artes una industria seria a tener en cuenta.En el encuentro han participado diversos agentes culturales del territorio rioj

In [0]:
train_limit = int(len(descripciones)*0.8)
val_limit = int(len(descripciones)*0.9)

In [0]:
df_trn = pd.DataFrame({'descripcion':descripciones[:train_limit], 'organizacion':etiquetas[:train_limit]}, columns=col_names)
df_val = pd.DataFrame({'descripcion':descripciones[train_limit:val_limit], 'organizacion':etiquetas[train_limit:val_limit]}, columns=col_names)
df_tst = pd.DataFrame({'descripcion':descripciones[val_limit:], 'organizacion':etiquetas[val_limit:]}, columns=col_names)

In [34]:
df_trn.head(15)

organizacion                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              descripcion
0             50  El director general de Cultura y Turismo, Eduardo Rodríguez Osés, ha presidido esta mañana en Riojaforum un encuentro con los principales agentes culturales del de La Rioja, con el objetivo de crear una red de trabajo y colaboración conjunta entre las diversas instituciones riojanas y las empresas profesionales de las artes escénicas en La Rioja. Con ello se busca promocionar la "marca teatro riojano" y facilitar el acceso de este sector a los circuitos de teatro de todo el ámbito nacional.Asimismo, en esta reunión, organizada por la Consejería de Desarrollo Económico e Innovación y la Aso...
1             50  El director general de Cultura y Turismo, Eduardo Rodríguez Osés, ha hecho un balance de la participación riojana en FITUR y se ha mostrado satisfecho de cómo han transcurrido los cinco días de feria en el stand del Gobierno de La Rioja. "FITUR es un magnífico escaparate en el que damos a conocer los atractivos turísticos que ofrece La Rioja al visitante y promocionamos nuestros productos más representativos, como el vino y otros productos gastronómicos, pero también, nuestros recursos culturales e idiomáticos, como los monasterios de San Millán o la próxima celebración de La Rioja Tierra ...
2             46  El Gobierno de La Rioja abrirá de forma inmediata el plazo de subsanación de documentación en el proceso de contratación del suministro de mobiliario del Palacio de Justicia de La Rioja.Esta mañana, el Tribunal Administrativo Central de Recursos Contractuales ha notificado al Ejecutivo riojano que se estimaba el recurso presentado por una UTE licitadora cuya oferta fue excluida por la Mesa de Contratación celebrada el pasado 13 de noviembre. El motivo de la exclusión fue que la UTE no aportó los certificados de calidad que se exigían en el Pliego de Prescripciones Técnicas.La resolución de...
3             24  El presidente del Gobierno regional, José Ignacio Ceniceros, ha participado hoy en el parque de bomberos de Nájera en la presentación de dos autobombas rurales pesadas (BRP) que ha adquirido el Consorcio para el Servicio de Extinción de Incendios, Salvamento y Protección de La Rioja (CEIS-Rioja) y que darán servicio, además de a este parque, al de Arnedo.Se trata de dos vehículos provenientes de otro servicio de extinción de incendios que han sido totalmente restaurados, modificados y mejorados para adaptarlos a su nuevo uso, de forma que puedan ser utilizados en actuaciones de carácter mi...
4             46  El Gobierno de La Rioja destinará 1.492.538 euros al contrato de servicios del centro de atención integral a personas con autismo, síndrome de Asperger y otras discapacidades afines Leo Kanner de Logroño para seguir trabajando en la plena inclusión, en todos los ámbitos de la sociedad, de las personas con Trastorno del Espectro Autista (TEA).La Asociación Riojana de Padres de Niños Autistas de Logroño (ARPA) gestiona desde 2008 este centro que ofrece a los usuarios y sus familias los recursos de centro de día y de residencia.En concreto, cuenta con 30 plazas de centro de día (20 utilizadas...
5             37  El director general de Cultura y Turismo, Eduardo Rodríguez Osés, ha presentado hoy junto al alcalde de Ezcaray, Gonzalo Abajo, y el programador Jesús Pérez-Caballero, el cartel y la programación de la 23 edición del Festival internacional de Jazz Villa de Ezcaray Memorial Ebbe

COPIADO

The pandas dataframe is used to store text data in a newly evolving standard format of label followed by text columns. This was influenced by a paper by Yann LeCun (LINK REQUIRED). Fastai adopts this new format for NLP datasets. In the case of IMDB, there is only one text column.

In [0]:
!mkdir -p output/{lm,clas}

In [0]:
OUTPUT_PATH=Path('./output')

TASSLM_PATH=OUTPUT_PATH/'lm'

CLAS_PATH=OUTPUT_PATH/'clas'

In [0]:
df_trn[df_trn['organizacion']!=0].to_csv(CLAS_PATH/'train.csv', header=False, index=False)
df_val[df_val['organizacion']!=0].to_csv(CLAS_PATH/'validation.csv', header=False, index=False)
df_tst[df_tst['organizacion']!=0].to_csv(CLAS_PATH/'test.csv', header=False, index=False)

(CLAS_PATH/'classes.txt').open('w').writelines(f'{o}\n' for o in str_labels)

In [0]:
df_trn = pd.DataFrame({'descripcion':descripciones[:train_limit], 'organizacion':[0]*len(organizaciones[:train_limit])}, columns=col_names)
df_val = pd.DataFrame({'descripcion':descripciones[train_limit:val_limit], 'organizacion':[0]*len(organizaciones[train_limit:val_limit])}, columns=col_names)
df_tst = pd.DataFrame({'descripcion':descripciones[val_limit:], 'organizacion':[0]*len(organizaciones[val_limit:])}, columns=col_names)

In [0]:
df_trn.to_csv(TASSLM_PATH/'train.csv', header=False, index=False)
df_val.to_csv(TASSLM_PATH/'validation.csv', header=False, index=False)
df_tst.to_csv(TASSLM_PATH/'test.csv', header=False, index=False)


## Tokenize and Standarize General Tokens for TASS Dataset


In [0]:
chunksize=24000

re1 = re.compile(r'  +')

In [0]:
def fixup(x):
    x = x.replace('#39;', "'").replace('amp;', '&').replace('#146;', "'").replace(
        'nbsp;', ' ').replace('#36;', '$').replace('\\n', "\n").replace('quot;', "'").replace(
        '<br />', "\n").replace('\\"', '"').replace('<unk>','u_n').replace(' @.@ ','.').replace(
        ' @-@ ','-').replace('\\', ' \\ ')
    return re1.sub(' ', html.unescape(x))

def get_texts(df, n_lbls=1):
    labels = df.iloc[:,range(n_lbls)].values.astype(np.int64)
    texts = f'\n{BOS} ' + df[n_lbls].astype(str)
    for i in range(n_lbls+1, len(df.columns)): texts += f' {FLD} {i-n_lbls} ' + df[i].astype(str)
    texts = texts.apply(fixup).values.astype(str)

    tok = Tokenizer('es')
    tok.proc_all_mp(partition_by_cores(texts), lang='es')
    return tok, list(labels)

def get_all(df, n_lbls):
    tok, labels = [], []
#     print(df)
    for i, r in enumerate(df):
        tok_, labels_ = get_texts(r, n_lbls)
        tok += tok_;
        labels += labels_
    return tok, labels

In [0]:
df_trn = pd.read_csv(TASSLM_PATH/'train.csv', header=None, chunksize=chunksize)
df_val = pd.read_csv(TASSLM_PATH/'validation.csv', header=None, chunksize=chunksize)

In [6]:
tok_trn, trn_labels = get_all(df_trn, 1)
tok_val, val_labels = get_all(df_val, 1)

AttributeError: ignored

In [62]:
print(tok_trn[:2])

[]
